In [1]:
!pip install -U cufflinks

Requirement already up-to-date: cufflinks in /usr/local/lib/python3.6/dist-packages (0.15)


In [0]:
import tensorflow as tf
import os

In [3]:
if tf.gfile.Exists('./fenwicks'):
  tf.gfile.DeleteRecursively('./fenwicks')
!git clone https://github.com/fenwickslab/fenwicks.git

import fenwicks as fw

Cloning into 'fenwicks'...
remote: Enumerating objects: 65, done.
remote: Counting objects: 100% (65/65), done.
remote: Compressing objects: 100% (46/46), done.
remote: Total 1286 (delta 37), reused 43 (delta 19), pack-reused 1221
Receiving objects: 100% (1286/1286), 17.96 MiB | 23.79 MiB/s, done.
Resolving deltas: 100% (770/770), done.


In [4]:
BUCKET = 'gs://gs_colab'
PROJECT = 'tutorial4'
MODEL = "InceptionResNetV2" #@param ["InceptionResNetV2", "ResNet50", "ResNet50V2", "InceptionV3", "MobileNetV2", "Xception"]

BATCH_SIZE = 128 #@param ["128", "256", "512"] {type:"raw"}
EPOCHS = 1 #@param {type:"slider", min:0, max:50, step:1}
LEARNING_RATE = 0.001 #@param ["0.001", "0.01"] {type:"raw"}

In [5]:
fw.colab_utils.setup_gcs()

In [6]:
data_dir, work_dir = fw.io.get_gcs_dirs(BUCKET, PROJECT)

In [7]:
base_model = fw.keras_models.get_model(MODEL, BUCKET)

In [8]:
data_dir_local = fw.datasets.untar_data(fw.datasets.URLs.DVC, os.path.join('.', PROJECT))
train_dir_local = os.path.join(data_dir_local, 'dogscats/train')
valid_dir_local = os.path.join(data_dir_local, 'dogscats/valid')

In [9]:
fw.preprocess.check_rgb(train_dir_local)
fw.preprocess.check_rgb(valid_dir_local)

In [10]:
train_fn = os.path.join(data_dir, 'train.tfrec')
valid_fn = os.path.join(data_dir, 'valid.tfrec')
paths_train, y_train, labels = fw.data.data_dir_tfrecord(train_dir_local, train_fn)
paths_valid, y_valid, _ = fw.data.data_dir_tfrecord(valid_dir_local, valid_fn)
n_train, n_valid = len(y_train), len(y_valid)
n_classes = len(labels)

INFO:tensorflow:Output file already exists. Skipping.
INFO:tensorflow:Output file already exists. Skipping.


In [11]:
fw.plt.plot_counts_pie(y_train, labels)

In [12]:
fw.anim.show_image_files(paths_train)

In [13]:
def build_nn(c=256):
  base = base_model.model_func()
  base.trainable = False  
  model = fw.Sequential()
  model.add(base)
  model.add(tf.keras.layers.Flatten())
  model.add(fw.layers.DenseBN(c))
  model.add(fw.layers.Classifier(n_classes))
  return model

In [14]:
total_steps = n_train // BATCH_SIZE * EPOCHS

In [15]:
lr_func = fw.train.cosine_lr(init_lr=LEARNING_RATE, total_steps=total_steps)
fw.plt.plot_lr_func(lr_func, total_steps=total_steps)

Instructions for updating:
Colocations handled automatically by placer.


In [16]:
opt_func = fw.train.adam_optimizer(lr_func)
model_func = fw.train.get_clf_model_func(build_nn, opt_func)

In [21]:
def get_input_func(fn, training):
  h = w = base_model.img_size
  tfms = fw.transform.get_inception_transforms(h, w, training=training, normalizer=base_model.normalizer)
  parser = fw.data.get_tfexample_image_parser(tfms)
  return lambda params: fw.data.tfrecord_ds(fn, parser, params['batch_size'], training=training)

train_input_func = get_input_func(train_fn, True)
valid_input_func = get_input_func(valid_fn, False)

In [19]:
est = fw.train.get_tpu_estimator(n_train // BATCH_SIZE,  model_func, work_dir, 
  base_model.weight_dir, base_model.weight_vars, trn_bs=BATCH_SIZE, val_bs=n_valid)

est.train(train_input_func, steps=total_steps)

INFO:tensorflow:Using config: {'_model_dir': 'gs://gs_colab/work/tutorial4/2019-05-08-15:22:50', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
cluster_def {
  job {
    name: "worker"
    tasks {
      key: 0
      value: "10.66.137.162:8470"
    }
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': None, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f62d662e518>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': 'grpc://10.66.137.162:8470', '_evaluation_master': 'grpc://10.66.137.162:8470', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1, '_tpu_config': TPUConfig(iterations_per_loop=179, num_shards=

In [22]:
result = est.evaluate(valid_input_func, steps=1)

INFO:tensorflow:Calling model_fn.
ERROR:tensorflow:Operation of type Placeholder (input_1) is not supported on the TPU. Execution will fail if this op is used in the graph. 
Instructions for updating:
Deprecated in favor of operator or tf.math.divide.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2019-05-08T15:27:38Z
INFO:tensorflow:TPU job name worker
INFO:tensorflow:Graph was finalized.
Instructions for updating:
Use standard file APIs to check for files with this prefix.
INFO:tensorflow:Restoring parameters from gs://gs_colab/work/tutorial4/2019-05-08-15:22:50/model.ckpt-179
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Init TPU system
INFO:tensorflow:Initialized TPU in 7 seconds
INFO:tensorflow:Starting infeed thread controller.
INFO:tensorflow:Starting outfeed thread controller.
INFO:tensorflow:Initialized dataset iterators in 0 seconds
INFO:tensorflow:Enqueue next (1) batch(es) of data to infeed.

In [23]:
print(f'Test results: accuracy={result["accuracy"] * 100: .2f}%, loss={result["loss"]: .2f}.')

Test results: accuracy= 99.20%, loss= 0.03.


In [24]:
fw.io.create_clean_dir(work_dir)